# Tarea 4 - Punto 4


# Descarga de Tensorflow para utilizar Keras.

In [1]:
# !pip3 install tensorflow

# Importar librerias necesarias.

In [2]:
import numpy as np
import pandas as pd
from keras.models import Sequential
from keras.layers import Embedding, Flatten, Dense, Dropout

from sklearn.model_selection import train_test_split
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense
import gensim
import os
from gensim.utils import simple_preprocess
from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences
from sklearn.preprocessing import LabelEncoder
from keras.layers import Dense, Embedding, Flatten
from keras.callbacks import EarlyStopping
import gensim.downloader 


## PREPROCESAMIENTO

## Carga de datos.

In [3]:


books_folder = './books/'


book_files = [f for f in os.listdir(books_folder) if f.endswith('.txt')]

names = []
books_texts = []
for book_file in book_files:
    with open(os.path.join(books_folder, book_file), 'r', encoding='utf-8') as file:
        books_texts.append(file.read())
        names.append(book_file.split('_')[0])

print(f'Se encontraron {len(book_files)} libros en la carpeta /books')
processed_books = [" ".join(simple_preprocess(text)) for text in books_texts]
processed_books



Se encontraron 9 libros en la carpeta /books


['introduction what thoughtful man has not been perplexed by problems relating to art an estimable and charming russian lady knew felt the charm of the music and ritual of the services of the russo greek church so strongly that she wished the peasants in whom she was interested to retain their blind faith though she herself disbelieved the church doctrines their lives are so poor and bare they have so little art so little poetry and colour in their lives let them at least enjoy what they have it would be cruel to undeceive them said she false and antiquated view of life is supported by means of art and is inseparably linked to some manifestations of art which we enjoy and prize if the false view of life be destroyed this art will cease to appear valuable is it best to screen the error for the sake of preserving the art or should the art be sacrificed for the sake of truthfulness again and again in history dominant church has utilised art to maintain its sway over men reformers early ch

## Separacion del conjunto de datos en fragmentos de 150 palabras.

Ademas, se añade la etiqueta a cada fragmento

In [4]:
def split_into_fragments(text, fragment_size=150):
    words = text.split()
    fragments = [words[i:i + fragment_size] for i in range(0, len(words), fragment_size)]
    return [' '.join(fragment) for fragment in fragments]


fragment_size = 150  
fragmented_books = []
fragment_labels = []

for i, book_text in enumerate(books_texts):
    fragments = split_into_fragments(book_text, fragment_size=fragment_size)
    fragmented_books.extend(fragments)
    fragment_labels.extend([names[i]] * len(fragments))  


## Conteo de fragmentos por cada autor

In [5]:
print(len(fragment_labels))
dic = {}
for i in fragment_labels:
    dic[i] = dic.get(i, 0)+ 1

print(dic)

7553
{'tolstoy': 4544, 'forster': 1520, 'vonarnin': 1489}


# Tokenizacion y transformacion de etiquetas a vectores

In [6]:
tokenizer = Tokenizer()
tokenizer.fit_on_texts(fragmented_books)
X = tokenizer.texts_to_sequences(fragmented_books)

X = pad_sequences(X, maxlen=fragment_size)

label_encoder = LabelEncoder()
y = label_encoder.fit_transform(fragment_labels)


## Separacion del conjunto de entrenamiento y testing

In [7]:
from imblearn.over_sampling import RandomOverSampler
ros = RandomOverSampler(random_state=42)
X_resampled, y_resampled = ros.fit_resample(X, y)

X_train, X_test, y_train, y_test = train_test_split(X_resampled, y_resampled, test_size=0.2, random_state=42, stratify=y_resampled)


In [8]:
vocab_size = len(tokenizer.word_index) + 1  


# Carga de emmbeddings.

In [9]:
glove_vectors = gensim.downloader.load('glove-wiki-gigaword-100')
glove_vectors_2 = gensim.downloader.load('glove-wiki-gigaword-200')
glove_vectors_3 = gensim.downloader.load('glove-wiki-gigaword-300')


In [10]:

# glove_vectors = gensim.downloader.load('word2vec-google-news-300')

In [11]:
embedding_model = glove_vectors
embedding_model_2 = glove_vectors_2
embedding_model_3 = glove_vectors_3



## Creacion de la matriz de embeddings a partir del vector de embeddings.

## Embeddings de tamaño 100

In [12]:
vocab_size = len(tokenizer.word_index) + 1  
embedding_dim = embedding_model.vector_size  
embedding_matrix = np.zeros((vocab_size, embedding_dim))

In [13]:
for word, idx in tokenizer.word_index.items():
    if word in glove_vectors:
        embedding_matrix[idx] = glove_vectors[word]


In [40]:
vocab_size = len(tokenizer.word_index) + 1  
vocab_size

35078

## Embeddings de tamaño 200

In [14]:
vocab_size = len(tokenizer.word_index) + 1  
embedding_dim_2 = embedding_model_2.vector_size  
embedding_matrix_2 = np.zeros((vocab_size, embedding_dim_2))

In [15]:
for word, idx in tokenizer.word_index.items():
    if word in glove_vectors_2:
        embedding_matrix_2[idx] = glove_vectors_2[word]

## Embeddings de tamaño 300

In [16]:
vocab_size = len(tokenizer.word_index) + 1  
embedding_dim_3 = embedding_model_3.vector_size  
embedding_matrix_3 = np.zeros((vocab_size, embedding_dim_3))

In [17]:
for word, idx in tokenizer.word_index.items():
    if word in glove_vectors_3:
        embedding_matrix_3[idx] = glove_vectors_3[word]

## Creacion de la red feedforward 2

# Embeddings de tamaño 100

In [18]:
model = Sequential()
model.add(Embedding(input_dim=vocab_size, 
                    output_dim=embedding_dim, 
                    weights=[embedding_matrix],  
                    input_length=fragment_size,  
                    trainable=False))  

model.add(Flatten()) 
model.add(Dense(128, activation='relu')) 
model.add(Dense(64, activation='relu'))   
model.add(Dense(len(set(names)), activation='softmax'))  #


In [19]:
model.compile(optimizer='adam', loss='sparse_categorical_crossentropy', metrics=['accuracy'])


# Embeddings de tamaño 200

In [20]:
model_2 = Sequential()
model_2.add(Embedding(input_dim=vocab_size, 
                    output_dim=embedding_dim_2, 
                    weights=[embedding_matrix_2],  
                    input_length=fragment_size,  
                    trainable=False))  

model_2.add(Flatten()) 
model_2.add(Dense(128, activation='relu')) 
model_2.add(Dense(64, activation='relu'))   
model_2.add(Dense(len(set(names)), activation='softmax'))  #

In [21]:
model_2.compile(optimizer='adam', loss='sparse_categorical_crossentropy', metrics=['accuracy'])

## Embeddings de tamaño 300

In [22]:
model_3 = Sequential()
model_3.add(Embedding(input_dim=vocab_size, 
                    output_dim=embedding_dim_3, 
                    weights=[embedding_matrix_3],  
                    input_length=fragment_size,  
                    trainable=False))  

model_3.add(Flatten()) 
model_3.add(Dense(128, activation='relu')) 
model_3.add(Dense(64, activation='relu'))   
model_3.add(Dense(len(set(names)), activation='softmax'))  #

In [23]:
model_3.compile(optimizer='adam', loss='sparse_categorical_crossentropy', metrics=['accuracy'])

## Correr el entrenamiento. 
Se agrega un moonitor para deter cuando el valor de perdida deja de disminuir.

In [24]:
early_stopping = EarlyStopping(monitor='val_loss', patience=5, restore_best_weights=True)

model.fit(X_train, y_train, epochs=100, batch_size=32, validation_data=(X_test[:32], y_test[:32]), callbacks=[early_stopping])


Epoch 1/100
341/341 [==============================] - 3s 7ms/step - loss: 0.6727 - accuracy: 0.7153 - val_loss: 0.5608 - val_accuracy: 0.7812
Epoch 2/100
341/341 [==============================] - 2s 6ms/step - loss: 0.1993 - accuracy: 0.9342 - val_loss: 0.5602 - val_accuracy: 0.9062
Epoch 3/100
341/341 [==============================] - 2s 6ms/step - loss: 0.0926 - accuracy: 0.9671 - val_loss: 0.5340 - val_accuracy: 0.8438
Epoch 4/100
341/341 [==============================] - 2s 5ms/step - loss: 0.0288 - accuracy: 0.9917 - val_loss: 0.5873 - val_accuracy: 0.8750
Epoch 5/100
341/341 [==============================] - 2s 5ms/step - loss: 0.0077 - accuracy: 0.9986 - val_loss: 0.5948 - val_accuracy: 0.8750
Epoch 6/100
341/341 [==============================] - 2s 5ms/step - loss: 0.0012 - accuracy: 0.9999 - val_loss: 0.7582 - val_accuracy: 0.8750
Epoch 7/100
341/341 [==============================] - 2s 5ms/step - loss: 2.9316e-04 - accuracy: 1.0000 - val_loss: 0.8010 - val_accuracy: 0.

In [25]:
early_stopping = EarlyStopping(monitor='val_loss', patience=5, restore_best_weights=True)

model_2.fit(X_train, y_train, epochs=100, batch_size=32, validation_data=(X_test[:32], y_test[:32]), callbacks=[early_stopping])


Epoch 1/100
341/341 [==============================] - 3s 9ms/step - loss: 0.5689 - accuracy: 0.7669 - val_loss: 0.5168 - val_accuracy: 0.8125
Epoch 2/100
341/341 [==============================] - 3s 9ms/step - loss: 0.0978 - accuracy: 0.9694 - val_loss: 0.9532 - val_accuracy: 0.7812
Epoch 3/100
341/341 [==============================] - 3s 9ms/step - loss: 0.0151 - accuracy: 0.9973 - val_loss: 0.7105 - val_accuracy: 0.8750
Epoch 4/100
341/341 [==============================] - 3s 9ms/step - loss: 0.0062 - accuracy: 0.9988 - val_loss: 0.6853 - val_accuracy: 0.8750
Epoch 5/100
341/341 [==============================] - 3s 10ms/step - loss: 0.0024 - accuracy: 0.9996 - val_loss: 0.9689 - val_accuracy: 0.8438
Epoch 6/100
341/341 [==============================] - 3s 10ms/step - loss: 6.8869e-04 - accuracy: 1.0000 - val_loss: 0.9786 - val_accuracy: 0.8438


In [26]:
early_stopping = EarlyStopping(monitor='val_loss', patience=5, restore_best_weights=True)

model_3.fit(X_train, y_train, epochs=100, batch_size=32, validation_data=(X_test[:32], y_test[:32]), callbacks=[early_stopping])


Epoch 1/100
341/341 [==============================] - 5s 14ms/step - loss: 0.5270 - accuracy: 0.7882 - val_loss: 0.5452 - val_accuracy: 0.8750
Epoch 2/100
341/341 [==============================] - 5s 15ms/step - loss: 0.0434 - accuracy: 0.9873 - val_loss: 0.7287 - val_accuracy: 0.8125
Epoch 3/100
341/341 [==============================] - 5s 14ms/step - loss: 0.0075 - accuracy: 0.9983 - val_loss: 0.9658 - val_accuracy: 0.8750
Epoch 4/100
341/341 [==============================] - 4s 13ms/step - loss: 0.0029 - accuracy: 0.9995 - val_loss: 0.8237 - val_accuracy: 0.8438
Epoch 5/100
341/341 [==============================] - 4s 13ms/step - loss: 0.0152 - accuracy: 0.9953 - val_loss: 0.9483 - val_accuracy: 0.8125
Epoch 6/100
341/341 [==============================] - 4s 13ms/step - loss: 0.1197 - accuracy: 0.9569 - val_loss: 0.9205 - val_accuracy: 0.8438


## Mostrar resultados

## Embeddings de tamaño 100

In [27]:
loss, accuracy = model.evaluate(X_test, y_test)

86/86 [==============================] - 0s 2ms/step - loss: 0.3139 - accuracy: 0.9146


In [28]:
model.summary()

Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 embedding (Embedding)       (None, 150, 100)          3507800   
                                                                 
 flatten (Flatten)           (None, 15000)             0         
                                                                 
 dense (Dense)               (None, 128)               1920128   
                                                                 
 dense_1 (Dense)             (None, 64)                8256      
                                                                 
 dense_2 (Dense)             (None, 3)                 195       
                                                                 
Total params: 5436379 (20.74 MB)
Trainable params: 1928579 (7.36 MB)
Non-trainable params: 3507800 (13.38 MB)
_________________________________________________________________


## Embeddings de tamaño 200

In [29]:
loss, accuracy = model_2.evaluate(X_test, y_test)

86/86 [==============================] - 0s 3ms/step - loss: 0.2982 - accuracy: 0.9010


In [30]:
model_2.summary()

Model: "sequential_1"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 embedding_1 (Embedding)     (None, 150, 200)          7015600   
                                                                 
 flatten_1 (Flatten)         (None, 30000)             0         
                                                                 
 dense_3 (Dense)             (None, 128)               3840128   
                                                                 
 dense_4 (Dense)             (None, 64)                8256      
                                                                 
 dense_5 (Dense)             (None, 3)                 195       
                                                                 
Total params: 10864179 (41.44 MB)
Trainable params: 3848579 (14.68 MB)
Non-trainable params: 7015600 (26.76 MB)
_________________________________________________________________


## Embeddings tamańo 300

In [31]:
loss, accuracy = model_3.evaluate(X_test, y_test)

86/86 [==============================] - 0s 3ms/step - loss: 0.2570 - accuracy: 0.9179


In [32]:
model_3.summary()

Model: "sequential_2"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 embedding_2 (Embedding)     (None, 150, 300)          10523400  
                                                                 
 flatten_2 (Flatten)         (None, 45000)             0         
                                                                 
 dense_6 (Dense)             (None, 128)               5760128   
                                                                 
 dense_7 (Dense)             (None, 64)                8256      
                                                                 
 dense_8 (Dense)             (None, 3)                 195       
                                                                 
Total params: 16291979 (62.15 MB)
Trainable params: 5768579 (22.01 MB)
Non-trainable params: 10523400 (40.14 MB)
_________________________________________________________________


# MEtricas


## Emnbeddings de tamaño 100


In [33]:
y_pred = model.predict(X_test)
y_pred_classes = np.argmax(y_pred, axis=1)

86/86 [==============================] - 0s 2ms/step


In [34]:
from sklearn.metrics import classification_report

print(classification_report(y_test, y_pred_classes))


              precision    recall  f1-score   support

           0       0.93      0.96      0.95       909
           1       0.95      0.83      0.88       909
           2       0.87      0.96      0.91       909

    accuracy                           0.91      2727
   macro avg       0.92      0.91      0.91      2727
weighted avg       0.92      0.91      0.91      2727



## Emnbeddings de tamaño 200


In [35]:
y_pred = model_2.predict(X_test)
y_pred_classes = np.argmax(y_pred, axis=1)  

86/86 [==============================] - 0s 3ms/step


In [36]:
from sklearn.metrics import classification_report

print(classification_report(y_test, y_pred_classes))

              precision    recall  f1-score   support

           0       0.84      0.97      0.90       909
           1       0.94      0.86      0.90       909
           2       0.95      0.88      0.91       909

    accuracy                           0.90      2727
   macro avg       0.91      0.90      0.90      2727
weighted avg       0.91      0.90      0.90      2727



In [37]:
y_pred = model_3.predict(X_test)
y_pred_classes = np.argmax(y_pred, axis=1)  

86/86 [==============================] - 1s 6ms/step


In [38]:
from sklearn.metrics import classification_report

print(classification_report(y_test, y_pred_classes))

              precision    recall  f1-score   support

           0       0.87      0.98      0.92       909
           1       0.92      0.92      0.92       909
           2       0.98      0.86      0.92       909

    accuracy                           0.92      2727
   macro avg       0.92      0.92      0.92      2727
weighted avg       0.92      0.92      0.92      2727

